In [ ]:
# For Google Colab
# Install folium package.
!pip install folium

In [ ]:
# For Google Colab
# Mount your Google drive and copy all files from "AI_HW2" directory
# in your Google drive to current directory.
from google.colab import drive
drive.mount('/content/gdrive')
!cp -r ./gdrive/MyDrive/AI_HW2/* .

In [187]:
# Don't change this part.
# For load graph information and show map
import folium
import pickle
def load_path_graph(path):
    with open('graph.pkl', 'rb') as f:
        graph = pickle.load(f)

    node_pairs = list(zip(path[:-1], path[1:]))
    lines = []
    for edge in graph:
        if (edge['u'], edge['v']) in node_pairs or  (edge['v'], edge['u']) in node_pairs:
            lines.append(edge['geometry'])
    return lines

In [188]:
# Part 1~4 and 6
# You can write your code in this file directly.
# Or you can wirte in new .py files and import it.
# ex: from astar import astar

#Create an adjacency dict
import csv 

adj = {}
dis = {}

with open('./edges.csv') as file:
    reader = csv.reader(file, delimiter=',')
    line_count = 0
    for row in reader:
        if line_count == 0:
            line_count = line_count + 1
            
        else:
            if row[0] in adj.keys():
                adj[row[0]].append(row[1])
                dis[row[0]].append(row[2])
            else:
                adj[row[0]] = []
                adj[row[0]].append(row[1])
                dis[row[0]] = []
                dis[row[0]].append(row[2])
                
            line_count = line_count + 1
        

In [189]:
# BFS implementation

from copy import deepcopy

def bfs(start, end):
    queue = []
    #[[route], distance, num_node]
    start_struct = [[start], 0, 1]
    queue.append(start_struct)
    
    visited = []
    
    while len(queue) != 0:
        temp = queue[0]
        queue.pop(0)
        
        #check if we reach the end point
        last_node = temp[0][len(temp[0]) - 1]
        if last_node == end:
            break
            
        #check if the node has already visited
        if last_node in visited:
            continue
        else:
            visited.append(last_node)
        
        #consider every node we can reach at the next step
        if last_node not in adj.keys():
            continue
            
        for i in range(len(adj[last_node])):
            next_struct = deepcopy(temp)
            next_struct[0].append(adj[last_node][i])
            next_struct[1] = next_struct[1] + float(dis[last_node][i])
            next_struct[2] = next_struct[2] + 1
            queue.append(next_struct)
            
    # transfer the return data type
    for i in range(len(temp[0])):
        temp[0][i] = int(temp[0][i])
        
    return temp[0], temp[1], temp[2]
        

In [244]:
# Part 5
# Change start ID and end ID.
start = str(2270143902)
end = str(1079387396)

In [200]:
# Don't change this part.
# Show the result of BFS
bfs_path, bfs_dist, bfs_visited = bfs(start, end)
print(f'The number of nodes in the path found by BFS: {len(bfs_path)}')
print(f'Total distance of path found by BFS: {bfs_dist} m')
print(f'The number of visited nodes in BFS: {bfs_visited}\n')

fmap = folium.Map(location=(24.806383132251874, 120.97685775516189), zoom_start=13)
for line in load_path_graph(bfs_path):
    fmap.add_child(folium.PolyLine(locations=line, tooltip='bfs', weight=4, color='blue'))
fmap

The number of nodes in the path found by BFS: 183
Total distance of path found by BFS: 15442.395000000002 m
The number of visited nodes in BFS: 183



In [291]:
# DFS implementation

visited = set()
result_path = []
result_distance = 0
result_sum = 0

def recursion(node_struct, end):
    last_node = node_struct[0][len(node_struct[0]) - 1]
    
    # check if we have already reached the end point
    if last_node == end:
        global result_path 
        result_path = node_struct[0]
        global result_distance 
        result_distance = node_struct[1]
        global result_sum 
        result_sum = node_struct[2]
        return True
     
    # check if the node is terminated
    if last_node not in adj.keys():
        return False
    
    # check if the node has already visited
    if last_node in visited:
        return False
    visited.add(last_node)
    
    # go through every neighbors
    for i in range(len(adj[last_node])):
        next_struct = deepcopy(node_struct)
        next_struct[0].append(adj[last_node][i])
        next_struct[1] = next_struct[1] + float(dis[last_node][i])
        next_struct[2] = next_struct[2] + 1
        
        if recursion(next_struct, end):
            return True
    
    return False
        
    
    

def dfs(start, end):
    
    #[[route], distance, num_node]
    start_struct = [[start], 0, 1]
    
    # call the recursive function
    if recursion(start_struct, end):
        
        # transfer the return data type
        for i in range(len(result_path)):
            result_path[i] = int(result_path[i])
        
        return result_path, result_distance, result_sum
        
    
    return [], -1, -1
    
    

In [292]:
# Don't change this part.
# Show the result of DFS
dfs_path, dfs_dist, dfs_visited = dfs(start, end)

print(f'The number of nodes in the path found by DFS: {len(dfs_path)}')
print(f'Total distance of path found by DFS: {dfs_dist} m')
print(f'The number of visited nodes in DFS: {dfs_visited}\n')

fmap = folium.Map(location=(24.806383132251874, 120.97685775516189), zoom_start=13)
for line in load_path_graph(dfs_path):
    fmap.add_child(folium.PolyLine(locations=line, tooltip='dfs', weight=4, color='green'))
fmap

The number of nodes in the path found by DFS: 1311
Total distance of path found by DFS: 48954.32100000007 m
The number of visited nodes in DFS: 1311



In [203]:
# UCS implementation

# get the element in queue which has the least distance
def get_min_struct_index(frontier):
    min_value = 100000000
    min_index = -1
    for i in range(len(frontier)):
        if frontier[i][1] < min_value:
            min_index = i
            min_value = frontier[i][1]
    return min_index

# check if the node is already in the frontier
def check_if_exist(node, frontier):
    for index in range(len(frontier)):
        if frontier[index][0][-1] == node:
            
            return True, index
        
    return False,  None
    
    
def ucs(start, end):
    path = []
    explored = []
    
    if start == end:
        return path, 0, 0
    
    path.append(start)
    
    # [path, distance, num_visited]
    frontier = [[path, 0, 1]]
    
    while len(frontier) > 0:
        min_index = get_min_struct_index(frontier)
        path_now = frontier[min_index][0].copy()
        distance_now = frontier[min_index][1]
        num_now = frontier[min_index][2]
        current_node = path_now[-1]
        
        frontier.pop(min_index)
        
        explored.append(current_node)
        
        # check if we reach the end
        if current_node == end:
            
            # transfer the return data type
            for i in range(len(path_now)):
                path_now[i] = int(path_now[i])
                
            return path_now, distance_now, frontier[min_index][2]
        
        # check if the point is terminated
        if current_node not in adj.keys():
            continue
        
        # go through every neighbors
        for i in range(len(adj[current_node])):
            next_node = adj[current_node][i]
            is_exist, exist_index = check_if_exist(next_node, frontier)
            
            next_path = path_now.copy()
            next_path.append(next_node)
            next_distance = distance_now + float(dis[current_node][i])
            
            # if the node is the new one which has never been explored
            if not is_exist and adj[current_node][i] not in explored:
                frontier.append([next_path, next_distance, num_now + 1])
            
            # if the node has already been explored 
            elif is_exist:
                if next_distance < frontier[exist_index][1]:
                    frontier.pop(exist_index)
                    frontier.append([next_path, next_distance, num_now + 1])
        
        
    

In [204]:
# Don't change this part.
# Show the result of UCS
ucs_path, ucs_dist, ucs_visited = ucs(start, end)
print(f'The number of nodes in the path found by UCS: {len(ucs_path)}')
print(f'Total distance of path found by UCS: {ucs_dist} m')
print(f'The number of visited nodes in UCS: {ucs_visited}\n')

fmap = folium.Map(location=(24.806383132251874, 120.97685775516189), zoom_start=13)
for line in load_path_graph(ucs_path):
    fmap.add_child(folium.PolyLine(locations=line, tooltip='ucs', weight=4, color='violet'))
fmap

The number of nodes in the path found by UCS: 288
Total distance of path found by UCS: 14212.412999999997 m
The number of visited nodes in UCS: 265



In [303]:
import csv 
ID1 = {}
ID2 = {}
ID3 = {}

# read the heuristic file
with open('./heuristic.csv') as file:
    reader = csv.reader(file, delimiter=',')
    line_count = 0
    for row in reader:
        if line_count == 0:
            line_count = line_count + 1

        else:

            ID1[row[0]] = row[1]
            ID2[row[0]] = row[2]
            ID3[row[0]] = row[3]
            line_count = line_count + 1
                

# sort all the neighbors by the estimate value
def least_cost(node, option):
    neighbor_unsorted = []
    
    # check if the node is terminated
    if node not in adj.keys():
        return []
    
    
    for i in range(len(adj[node])):
        # estimate by the destination
        if option == 1: 
            estimate = float(dis[node][i]) + float(ID1[adj[node][i]])
            neighbor_unsorted.append([i, estimate])
        elif option == 2:
            estimate = float(dis[node][i]) + float(ID2[adj[node][i]])
            neighbor_unsorted.append([i, estimate])
        else:
            estimate = float(dis[node][i]) + float(ID3[adj[node][i]])
            neighbor_unsorted.append([i, estimate])
        
    neighbor_sorted = sorted(neighbor_unsorted, key = lambda k : k[1])

    return neighbor_sorted
    
visited = set()
result_path = []
result_distance = 0
result_sum = 0

def recursion(node_struct, end, option):
    last_node = node_struct[0][len(node_struct[0]) - 1]
    
    # limit the recursion depth to prevent python code from crashing
    if node_struct[2] > 2500:
        return False

    if last_node == end:
        global result_path 
        result_path = node_struct[0]
        global result_distance 
        result_distance = node_struct[1]
        global result_sum 
        result_sum = node_struct[2]
        return True
    
    # ckeck if the point is terminated
    if last_node not in adj.keys():
        return False
    
    # check is the point has already visited
    if last_node in visited:
        return False
    visited.add(last_node)
    
    # sort by g(x) + h(x)
    neighbors = least_cost(last_node, option)
    
    
    for comb in neighbors:
        i = comb[0]
        next_struct = deepcopy(node_struct)
        next_struct[0].append(adj[last_node][i])
        next_struct[1] = next_struct[1] + float(dis[last_node][i])
        next_struct[2] = next_struct[2] + 1
        
        if recursion(next_struct, end, option):
            return True
    
    return False
        
    
    

def astar(start, end):
    #[[route], distance, num_node]
    start_struct = [[start], 0, 1]
    
    # we have three destination
    option = 0
    if end == "1079387396":
        option = 1
    elif end == "1737223506":
        option = 2
    else:
        option = 3
        
    if recursion(start_struct, end, option):
        
        # transfer the return data type
        for i in range(len(result_path)):
            result_path[i] = int(result_path[i])
        
        return result_path, result_distance, result_sum
        
    
    return [], -1, -1
        
    

In [304]:
# Don't change this part.
# Show the result of A* search
astar_path, astar_dist, astar_visited = astar(start, end)
print(f'The number of nodes in the path found by A* search: {len(astar_path)}')
print(f'Total distance of path found by A* search: {astar_dist} m')
print(f'The number of visited nodes in A* search: {astar_visited}\n')

fmap = folium.Map(location=(24.806383132251874, 120.97685775516189), zoom_start=13)
for line in load_path_graph(astar_path):
    fmap.add_child(folium.PolyLine(locations=line, tooltip='astar', weight=4, color='red'))
fmap

The number of nodes in the path found by A* search: 181
Total distance of path found by A* search: 8865.051999999998 m
The number of visited nodes in A* search: 181



In [207]:
# Part 6 (Bonus)
# Don't change this part.
# Show the shortest time result of A* search
time_path, time, time_visited = astar_time(start, end)
print(f'The number of nodes in the path found by A* search: {len(time_path)}')
print(f'Total second of path found by A* search: {time} s')
print(f'The number of visited nodes in A* search: {time_visited}\n')

fmap = folium.Map(location=(24.806383132251874, 120.97685775516189), zoom_start=13)
for line in load_path_graph(time_path):
    fmap.add_child(folium.PolyLine(locations=line, tooltip='astar', weight=4, color='red'))
fmap

NameError: name 'astar_time' is not defined

In [ ]:
# For Google Colab
# Remember to execute this line once you've modified any .py file
# Save the .py code you have modified to your Google Drive
!cp ./*.py ./gdrive/MyDrive/AI_HW2/